In [4]:
import requests
import json
import numpy as np
import pandas as pd
import config as cfg
import math

#import folium
#import ipywidgets as widgets
#from ipywidgets import Layout
#import matplotlib.pyplot as plt
import plotly.graph_objects as go

#from ipyleaflet import Map, basemaps, basemap_to_tiles, DrawControl, Polyline, TileLayer, GeoJSON, AntPath, Marker, Icon, Circle, CircleMarker

In [5]:
par = {
        "key":cfg.conf['key_TT2'],
    #     "callback":callback,
    #     "fuelBudgetInLiters":float,
        "maxChargeInkWh": 95,
        "currentChargeInkWh" : 80,
    #     "timeBudgetInSec":float,
    #     "distanceBudgetInMeters":float,
    #     "report":effectiveSettings,
    #     "departAt":time,
    #     "routeType":routeType,
        "traffic": "true",
        "avoid": "unpavedRoads",
        "travelMode": "car",
    #     "hilliness":hilliness,
    #     "windingness":windingness,
        "vehicleMaxSpeed": 200,
        "vehicleWeight": 2000,
        "vehicleAxleWeight": 1000,
        "vehicleLength": 3,
        "vehicleWidth": 2,
        "vehicleHeight": 1.5,
        "vehicleCommercial": "true",
    #     "vehicleLoadType":vehicleLoadType,
    #     "vehicleAdrTunnelRestrictionCode":vehicleAdrTunnelRestrictionCode,
        "vehicleEngineType":"electric",
    #     "constantSpeedConsumptionInLitersPerHundredkm":CombustionConstantSpeedConsumptionPairs,
    #     "currentFuelInLiters":float,
    #     "auxiliaryPowerInLitersPerHour":float,
    #     "fuelEnergyDensityInMJoulesPerLiter":float,
    #     "accelerationEfficiency":float,
    #     "decelerationEfficiency":float,
    #     "uphillEfficiency":float,
    #     "downhillEfficiency":float,
        #"velocityOffsetUnlimitedHighway":20,
        #"velocityOffsetFRC1":15,
        #"velocityOffsetFRC2":10,
        #"velocityOffsetFRC3":8,
        #"velocityOffsetFRC4":0,
        #"velocityOffsetFRC5":0,
        "constantSpeedConsumptionInkWhPerHundredkm": '0,29.4:27,27.9:45,29.4:60,23.1:75,24.7:90,27.8:100,29.5:110,31.55:120,34.35:130,35.55',
    #     "currentChargeInkWh":float,
    #     "maxChargeInkWh":float,
         "auxiliaryPowerInkW": 3,
    }

In [6]:
def response_url(url,parameters,cfg,headers=-1,payload=-1):
    try:
        if headers==-1 and payload==-1: # only get ...
            response = requests.get(url,params=parameters,timeout=300)#,proxies=cfg.conf['proxies'])
        else: # post with headers + json ...
            #response = requests.post(url,params=parameters,headers=headers,json=payload,timeout=300,proxies=cfg.conf['proxies'])
            response = requests.post(url,params=parameters,headers=headers,json=payload,timeout=300)
        response.raise_for_status()                 # Raise error in case of failure 
    except requests.exceptions.HTTPError as httpErr: 
        print ("Http Error:",httpErr) 
        print(response.json())
    except requests.exceptions.ConnectionError as connErr: 
        print ("Error Connecting:",connErr) 
    except requests.exceptions.Timeout as timeOutErr: 
        print ("Timeout Error:",timeOutErr) 
    except requests.exceptions.RequestException as reqErr: 
        print ("Something Else:",reqErr) 
    #print(response.url)
    #print(response.json())
    return response.json()

# Geocoding
def Mapbox_Geocoding(City_str):
    url = 'https://api.mapbox.com/geocoding/v5/mapbox.places/' + City_str + '.json'
    parameters = {'access_token':cfg.conf['key_MapBox']}
    return response_url(url,parameters,cfg)['features'][0]['center']

# TT EV HCP3 routing
def TomTom_HCP3_Routing(lat_s,lng_s,lat_d,lng_d,cfg,parameters):

    url = "https://api.tomtom.com/routing-hcp3/1//calculateRoute/" + str(lat_s)+ ',' +str(lng_s)+":"+str(lat_d)+ ',' +str(lng_d) + "/json?"

    response = response_url(url,parameters,cfg)#,headers,payload)
    #print(response)
    # data frame
    df = pd.DataFrame(data=response['routes'][0]['legs'][0]['points'], columns=['latitude','longitude']) # legs[0]
    
    # single values 
    singVal = [] 
    singValName = []
    singValName.append('batteryConsumptionInkWh_summary')
    singVal.append(response['routes'][0]['summary']['batteryConsumptionInkWh'])
    singValName.append('lengthInKiloMeters_summary')
    singVal.append(response['routes'][0]['summary']['lengthInMeters']/1000) # km
    singValName.append('travelTimeInMinutes_summary')
    singVal.append(response['routes'][0]['summary']['travelTimeInSeconds']/60) # min
    singValName.append('trafficDelayInMinutes_summary')
    singVal.append(response['routes'][0]['summary']['trafficDelayInSeconds']/60) # min
    df2 = pd.DataFrame(columns=singValName)
    df2.loc[0] = singVal
       
    return df,df2


In [7]:
lng_s,lat_s = Mapbox_Geocoding('Pascalstraße 7, 85057 Ingolstadt') # Only Germany ...
lng_d,lat_d = Mapbox_Geocoding('Ettinger Str. 26A, 85057 Ingolstadt') # Only Germany ...

df,df2 = TomTom_HCP3_Routing(lat_s,lng_s,lat_d,lng_d,cfg,par)

fig = go.Figure(go.Scattermapbox(
    mode = "markers+lines+text",
    lon = df.longitude,
    lat = df.latitude,
    marker = {'size': 8, 'color':'rgb(180,50,50)','opacity' : 0.25},
    text='TT HCP3 Routing',
    name='TomTom Routing'
    ))
fig.add_trace(go.Scattermapbox(
    mode = "markers",
    lon = [str(lng_d)],
    lat = [str(lat_d)],
    marker = {'size': 25, 'color':'rgb(180,50,50)','opacity' : 0.8},
    text='TT HCP3 Routing',
    name='TomTom Routing'
    ))
fig.add_trace(go.Scattermapbox(
    mode = "markers",
    lon = [str(lng_s)],
    lat = [str(lat_s)],
    marker = {'size': 25, 'color':'rgb(180,50,50)','opacity' : 0.8},
    text='TT HCP3 Routing',
    name='TomTom Routing'
    ))
fig.update_layout(
    margin ={'l':0,'t':0,'b':0,'r':0},
    mapbox = {
        'center': {'lon': lng_s, 'lat': lat_s},
        'style': "stamen-terrain",
        'center': {'lon': lng_d, 'lat': lat_d},
        'zoom': 10})

fig.show()